In [1]:
import discretisedfield as df
import micromagneticmodel as mm
import numpy as np
import oommfc as oc

https://www.sciencedirect.com/science/article/pii/S0304885319314246#f0015

In [13]:
cell = (2e-9, 2e-9, 1e-9)

subregions = {'top': df.Region(p1=(0, 0, 0), p2=(512e-9, 128e-9, 1e-9)),
              'spacer': df.Region(p1=(0, 0, -1e-9), p2=(512e-9, 128e-9, 0)),
              'bottom': df.Region(p1=(0, 0, -2e-9), p2=(512e-9, 128e-9, -1e-9))}
p1 = (0, 0, -2e-9)
p2 = (512e-9, 128e-9, 1e-9)
mesh = df.Mesh(p1=p1, p2=p2, cell=cell, subregions=subregions, bc='x')

In [14]:
mesh.n

(256, 64, 3)

In [15]:
system = mm.System(name='SAF')

Ms = 580e3 #1.2e6
A = 15e-12 #10e-12
D = 3.2e-3 #0.3e-3
K = 800e3 #0.905e6

j_af = -1.5e-3

alpha = 0.03
system.energy = (mm.Exchange(A=A) + 
                 mm.DMI(D=D, crystalclass='Cnv_z') + 
                 mm.RKKY(sigma=j_af, sigma2=0, subregions=['top', 'bottom']) + 
                 mm.UniaxialAnisotropy(K=K, u=(0,0,1)) + 
                 mm.Demag())

system.dynamics = mm.Precession(gamma0=mm.consts.gamma0) + mm.Damping(alpha=0.1)

In [16]:
np.random.seed(0)
def m_fun(pos):
    x, y, z = pos
    if z < 0:
        if (x-2.64e-7)**2 + (y-0.64e-7)**2 < (10e-9)**2:
            return (0, 0, 1)
        else:
            return (0, 0, -1)
    else:
        if (x-2.64e-7)**2 + (y-0.64e-7)**2 < (10e-9)**2:
            return (0, 0, -1)
        else:
            return (0, 0, 1)

norm = {'bottom': Ms, 'top': Ms, 'spacer': 0}
m_dir = {'bottom': (0,0.1,-0.9), 'top': (0,0.1,0.9), 'spacer': (0,0,1)}
system.m = df.Field(mesh, dim=3, value=m_fun, norm=norm)

In [17]:
system.m.hv(kdims=['x', 'y'])

:DynamicMap   [z]
   :Overlay
      .Image.I       :Image   [x,y]   (field)
      .VectorField.I :VectorField   [x,y]   (angle,mag)

In [18]:
md = oc.MinDriver()
md.drive(system, n_threads=16)

Running OOMMF (ExeOOMMFRunner)[2022/06/13 13:14]... (8.5 s)


In [19]:
system.m.hv(kdims=['x', 'y'])

:DynamicMap   [z]
   :Overlay
      .Image.I       :Image   [x,y]   (field)
      .VectorField.I :VectorField   [x,y]   (angle,mag)

# Drive with current

Find better parameters

In [20]:
ux = 400  # velocity in x-direction (m/s)
beta = 0.5  # non-adiabatic STT parameter

system.dynamics += mm.ZhangLi(u=ux, beta=beta)

In [21]:
td = oc.TimeDriver()
td.drive(system, t=1e-9, n=1000, verbose=2)

Running OOMMF (ExeOOMMFRunner):   0%|          | 0/1000 files written [00:00]

RuntimeError: Error in OOMMF run.
command: /home/sam/miniconda3/envs/ubermagdev/bin/oommf boxsi +fg SAF.mif -exitondone 1
stdout: Start: "/home/sam/repos/ubermag-devtools/repos/workshop/tutorials/SAF/drive-33/SAF.mif"
Options: -exitondone 1 -threads 4
Boxsi version 2.0a3
Running on: sam-OptiPlex
OS/machine: Linux/x86_64
User: sam	PID: 2882077
Number of threads: 4
Mesh geometry: 256 x 64 x 3 = 49 152 cells
Checkpoint file: /home/sam/repos/ubermag-devtools/repos/workshop/tutorials/SAF/drive-33/SAF.restart
Boxsi run end.

stderr: Logging to file "/home/sam/miniconda3/envs/ubermagdev/opt/oommf/boxsi.errors"

[Boxsi<2882077-sam-OptiPlex-sam> 13:14:54.683 2022-06-13] 2.0a3 infolog:
Start: "/home/sam/repos/ubermag-devtools/repos/workshop/tutorials/SAF/drive-33/SAF.mif"
Options: -exitondone 1 -threads 4

[Boxsi<2882077-sam-OptiPlex-sam> 13:14:54.720 2022-06-13] 2.0a3 infolog:
Boxsi version 2.0a3
Running on: sam-OptiPlex
OS/machine: Linux/x86_64
User: sam	PID: 2882077
Number of threads: 4
Mesh 

In [11]:
import micromagneticdata as md

data = md.Data(system.name)

In [12]:
data[-1].hv(kdims=['x','y'], vdims=['x','y'], scalar_kw = {'clim':(-Ms, Ms), 'cmap': 'coolwarm'})

:DynamicMap   [t,z]
   :Overlay
      .Image.I       :Image   [x,y]   (field)
      .VectorField.I :VectorField   [x,y]   (angle,mag)

In [ ]:
import mag2exp

In [ ]:
mfm_setup = data[-1][0].pad({'z': (0, 50)}, mode='constant')

In [ ]:
mfm_setup.hv(kdims=['x', 'y'])

In [ ]:
mfm_phase = mag2exp.mfm.phase_shift(mfm_setup, quality=650, k=3, tip_m=(0, 0, 1e-16))

In [ ]:
mfm_phase.hv(kdims=['x', 'y'])

In [ ]:
mfm_phase_q = mag2exp.mfm.phase_shift(mfm_setup, quality=650, k=3, tip_q=1e-8)

In [ ]:
mfm_phase_q.hv(kdims=['x', 'y'])

In [ ]:
mfm_phase_x = mag2exp.mfm.phase_shift(mfm_setup, quality=650, k=3, tip_m=(1e-16, 0, 0))

In [ ]:
mfm_phase_x.hv(kdims=['x', 'y'])

In [ ]:
mag2exp.quick_plots.x_ray_holography(data[-1][0], fwhm=(25e-9, 25e-9))

In [ ]:
field_rotator = df.FieldRotator(data[-1][0])
field_rotator.rotate("from_euler", seq="y", angles=10, degrees=True)
mag2exp.quick_plots.x_ray_holography(field_rotator.field, fwhm=(25e-9, 25e-9))

In [ ]:
field_rotator.field.norm.k3d.nonzero()